# Reinforcement Learning control strategies for Electric Vehicles fleet Virtual Power Plants
Thesis based on the development of a RL agent that manages a VPP through EVs charging stations in an household environment. Main optimization objectives of the VPP are: Valley filling, peak shaving and zero resulting load over time. Main action performed to reach objectives are: storage of Renewable energy resources and power push in the grid at high demand times. The development of the Virtual Power Plant environment is based on the ELVIS (Electric Vehicles Infrastructure Simulator) open library from DAI-Labor: https://github.com/dailab/elvis The thesis code is currently available at: (https://github.com/francescomaldonato/RL_VPP_Thesis)

Author: Francesco Maldonato

## VPP simulator Notebook based on EVs arrival, with StableBaselines3 trained model (Recurrent PPO) [25 EVs per week test]

Installing required packages and dependencies

In [1]:
%%capture
!pip install py-elvis==0.2.1
!pip install pyyaml==5.4
!pip install plotly==5.9.0
!pip install -U kaleido==0.2.1

!pip install stable-baselines3[extra]==1.6.1
!pip install stable-baselines==1.6.1
!pip install sb3-contrib==1.6.1
!pip install gym==0.20.0
!pip install -q wandb==0.13.4

In [2]:
#Cloning repository and changing directory
!git clone https://github.com/francescomaldonato/RL_VPP_Thesis.git
%cd RL_VPP_Thesis/
%ls

Cloning into 'RL_VPP_Thesis'...
remote: Enumerating objects: 399, done.
remote: Counting objects: 100% (6/6), done.
remote: Compressing objects: 100% (6/6), done.
remote: Total 399 (delta 0), reused 2 (delta 0), pack-reused 393
Receiving objects: 100% (399/399), 151.25 MiB | 22.16 MiB/s, done.
Resolving deltas: 100% (149/149), done.
Checking out files: 100% (108/108), done.
/content/RL_VPP_Thesis
Agent_trainer_notebooks/          README.md             VPP_environment.py
data/                             Simulator_notebooks/  VPP_simulator.ipynb
Hyperparameters_sweep_notebooks/  trained_models/       wandb/


In [3]:
import yaml
import numpy as np
from gym import Env
from VPP_environment import VPPEnv, VPP_Scenario_config
from elvis.config import ScenarioConfig
import os
import torch
import random
import wandb
from sb3_contrib import RecurrentPPO #The available algoritmhs in sb3-contrib for the custom environment with MultiInputPolicy
from sb3_contrib.common.maskable.utils import get_action_masks
import stable_baselines3 as sb3
from stable_baselines3.common.env_checker import check_env

#Check if cuda device is available for training
print("Torch-Cuda available device:", torch.cuda.is_available())
print(sb3.get_system_info())
#!wandb --version

Torch-Cuda available device: False
OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022
Python: 3.7.14
Stable-Baselines3: 1.6.1
PyTorch: 1.12.1+cu113
GPU Enabled: False
Numpy: 1.21.6
Gym: 0.20.0

({'OS': 'Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022', 'Python': '3.7.14', 'Stable-Baselines3': '1.6.1', 'PyTorch': '1.12.1+cu113', 'GPU Enabled': 'False', 'Numpy': '1.21.6', 'Gym': '0.20.0'}, 'OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022\nPython: 3.7.14\nStable-Baselines3: 1.6.1\nPyTorch: 1.12.1+cu113\nGPU Enabled: False\nNumpy: 1.21.6\nGym: 0.20.0\n')


In [4]:
# Ensure deterministic behavior
torch.backends.cudnn.deterministic = True
random.seed(0)
torch.manual_seed(0)
torch.cuda.manual_seed_all(0)

## Load ELVIS YAML config file
Section where the EVs arrival simulation parameters are loaded through the Yaml config file from the 'data/config_builder/' folder.

In [5]:
#Loading paths for input data
current_folder = ''
VPP_training_data_input_path = current_folder + 'data/data_training/environment_table/' + 'Environment_data_2019.csv'
VPP_testing_data_input_path = current_folder + 'data/data_testing/environment_table/' + 'Environment_data_2020.csv'
VPP_validating_data_input_path = current_folder + 'data/data_validating/environment_table/' + 'Environment_data_2018.csv'
elvis_input_folder = current_folder + 'data/config_builder/'

#case = 'wohnblock_household_simulation_adaptive.yaml' #(loaded by default, 20 EVs arrivals per week with 50% average battery)

#Try different simulation parameters, uncomment below
#case = 'wohnblock_household_simulation_adaptive_10.yaml' #(10 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_15.yaml' #(15 EVs arrivals per week with 50% average battery)
case = 'wohnblock_household_simulation_adaptive_25.yaml' #(25 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_30.yaml' #(30 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_35.yaml' #(35 EVs arrivals per week with 50% average battery) 

with open(elvis_input_folder + case, 'r') as file:
    yaml_str = yaml.full_load(file)

elvis_config_file = ScenarioConfig.from_yaml(yaml_str)
VPP_config_file = VPP_Scenario_config(yaml_str)

print(elvis_config_file)
print(VPP_config_file)

Vehicle types: <generator object ScenarioConfig.__str__.<locals>.<genexpr> at 0x7f445e27a950>Mean parking time: 23.99
Std deviation of parking time: 1
Mean value of the SOC distribution: 0.5
Std deviation of the SOC distribution: 0.1
Max parking time: 24
Number of charging events per week: 25
Vehicles are disconnected only depending on their parking time
Queue length: 0
Opening hours: None
Scheduling policy: Uncontrolled

{'start_date': '2022-01-01T00:00:00', 'end_date': '2023-01-01T00:00:00', 'resolution': '0:15:00', 'num_households': 4, 'solar_power': 16, 'wind_power': 12, 'EV_types': [{'battery': {'capacity': 100, 'efficiency': 1, 'max_charge_power': 150, 'min_charge_power': 0}, 'brand': 'Tesla', 'model': 'Model S', 'probability': 1}], 'charging_stations_n': 4, 'EVs_n': 25, 'EVs_n_max': 1305, 'mean_park': 23.99, 'std_deviation_park': 1, 'EVs_mean_soc': 50.0, 'EVs_std_deviation_soc': 10.0, 'EV_load_max': 44, 'EV_load_rated': 14.8, 'EV_load_min': 1, 'houseRWload_max': 10, 'av_max_ener

In [6]:
#TESTING Environment initialization
env = VPPEnv(VPP_testing_data_input_path, elvis_config_file, VPP_config_file)
env.plot_VPP_input_data()

Output hidden; open in https://colab.research.google.com to view.

In [7]:
env.plot_ELVIS_data()

In [8]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
env.plot_reward_functions()

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  27508.6 , over-consume=kWh  43850.62 , under-consume=kWh  16342.03 , Total_cost=€  1051.92 , overcost=€  1521.7 , Av.EV_en_left=kWh  100.0 , Charging_events=  1304 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  70.06
Simulating VPP....


### VPP Simulation test with random actions [no model loaded]

In [9]:
episodes = 1
for episode in range(1, episodes+1):
    state = env.reset()
    done = False
    score = 0
    while not done:
        action_masks = get_action_masks(env)
        action = env.action_space.sample()
        
        n_state, reward, done, info = env.step(action)
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [10]:
env.plot_Elvis_results()

Output hidden; open in https://colab.research.google.com to view.

In [11]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [12]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [13]:
env.plot_VPP_Elvis_comparison()

In [14]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [15]:
#env.plot_rewards_stats()

In [16]:
env.plot_EVs_kpi()

In [17]:
env.plot_actions_kpi()

In [18]:
env.plot_load_kpi()

In [19]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [20]:
## Wandb login to load models
#In Colab, uncomment below:
# %env "WANDB_DISABLE_CODE" True
# %env "WANDB_NOTEBOOK_NAME" "VPP_simulator.ipynb"
# os.environ['WANDB_NOTEBOOK_NAME'] = 'VPP_simulator.ipynb'
#wandb.login(relogin=True)

#In local notebook, uncomment below:
#your_wandb_login_code = 0123456789abcdefghijklmnopqrstwxyzàèìòù0 #example length
#!wandb login {your_wandb_login_code}

In [21]:
#Loading training model, from local directory or from wandb previous trainings
RecurrentPPO_path = "trained_models/RecurrentPPO_models/model_RecurrentPPO_"

#model_id = "s37o8q0n"
model_id = "333ckz0i"
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

# run_id_restore = "2y2dqvyn"
# model = wandb.restore(f'model_{run_id_restore}.zip', run_path=f"francesco_maldonato/RL_VPP_Thesis/{run_id_restore}")

/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


## Testing dataset VPP Simulation using the loaded trained model

In [22]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

#Save the VPP table
VPP_table = env.save_VPP_table(save_path='data/environment_optimized_output/VPP_table.csv')

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  26526.09 , over-consume=kWh  42711.74 , under-consume=kWh  16185.64 , Total_cost=€  1028.74 , overcost=€  1506.49 , Av.EV_en_left=kWh  100.0 , Charging_events=  1304 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  70.06
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -2760.03 , over-consume=KWh  1772.02 , under-consume=KWh  4532.05 , Total_cost=€  -46.44 , Overcost=€  62.1 
 EV_INFO: Av.EV_energy_leaving=kWh  64.71 , Std.EV_energy_leaving=kWh  23.72 , EV_departures =  1303 , EV_queue_left =  1
SCORE:  Cumulative_reward= 445134.85 - Step_rewars (load_t= 402973.42, EVs_energy_t= 13051.2)
 - Final_rewards (EVs_energy= 19319.5, Overconsume= -877.06, Underconsume= -1500.08, Overcost= 12167.86)
Episode:1 Score:445134.8528650521


In [23]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [24]:
VPP_table.head(15000)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00  31.434156  53.362289  65.852692  54.351841   
2022-01-01 00:15:00  31.684156  52.812973  65.303375  54.601841   
2022-01-01 00:30:00  31.934156  52.385311  64.875710  54.851841   
2022-01-01 00:45:00  32.184158  51.992237  64.482635  55.101841   
2022-01-01 01:00:00  32.434158  51.613438  64.103836  55.351841   
...                        ...        ...        ...        ...   
2022-06-06 04:45:00  99.989998  44.091381  80.841843  76.652328   
2022-06-06 05:00:00  99.989998  43.841381  81.919701  77.730186   
2022-06-06 05:15:00  99.989998  43.591381  83.585831  79.396317   
2022-06-06 05:30:00  99.989998  43.591381  84.579185  80.389671   
2022-06-06 05:45:00  99.989998  43.591381  85.563110  81.373596   

                                       EVs_id       actions  \
time                                                          
2022-01-01 00:00:00              [0, 0, 0, 0]  [1, 2, 2, 1]   
2022-01-01 00:15:00  [3908, 3911, 3910, 3909]  [1, 2, 2, 1]   
2022-01-01 00:30:00  [3908, 3911, 3910, 3909]  [1, 2, 2, 1]   
2022-01-01 00:45:00  [3908, 3911, 3910, 3909]  [1, 2, 2, 1]   
2022-01-01 01:00:00  [3908, 3911, 3910, 3909]  [1, 2, 2, 1]   
...                                       ...           ...   
2022-06-06 04:45:00  [4468, 4471, 4470, 4469]  [1, 2, 1, 1]   
2022-06-06 05:00:00  [4468, 4471, 4470, 4469]  [0, 2, 1, 1]   
2022-06-06 05:15:00  [4468, 4471, 4470, 4469]  [1, 0, 1, 1]   
2022-06-06 05:30:00  [4468, 4471, 4470, 4469]  [1, 0, 1, 1]   
2022-06-06 05:45:00  [4468, 4471, 4470, 4469]  [1, 2, 1, 1]   

                                       mask_truth  ev_charged_pwr  \
time                                                                
2022-01-01 00:00:00  [False, False, False, False]        0.000000   
2022-01-01 00:15:00    [False, True, True, False]        2.000000   
2022-01-01 00:30:00    [False, True, True, False]        2.000000   
2022-01-01 00:45:00    [False, True, True, False]        2.000000   
2022-01-01 01:00:00    [False, True, True, False]        2.000000   
...                                           ...             ...   
2022-06-06 04:45:00    [False, False, True, True]        9.883476   
2022-06-06 05:00:00     [True, False, True, True]        8.622857   
2022-06-06 05:15:00    [False, False, True, True]       13.329070   
2022-06-06 05:30:00    [False, False, True, True]        7.946833   
2022-06-06 05:45:00    [False, False, True, True]        7.871392   

                     ev_discharged_pwr          load  load_reward  EV_reward  \
time                                                                           
2022-01-01 00:00:00           0.000000  2.552690e+00    15.000000        0.0   
2022-01-01 00:15:00          -4.394546  4.440892e-16    15.000000        0.0   
2022-01-01 00:30:00          -3.421298  0.000000e+00    15.000000        0.0   
2022-01-01 00:45:00          -3.144600  0.000000e+00    15.000000        0.0   
2022-01-01 01:00:00          -3.030390  0.000000e+00    15.000000        0.0   
...                                ...           ...          ...        ...   
2022-06-06 04:45:00          -1.000000  0.000000e+00    -5.283105        0.0   
2022-06-06 05:00:00          -1.000000 -4.311415e+00    15.000000        0.0   
2022-06-06 05:15:00          -1.000000  0.000000e+00    -4.955673        0.0   
2022-06-06 05:30:00           0.000000 -3.973404e+00    -4.892805        0.0   
2022-06-06 05:45:00           0.000000 -3.935683e+00    -5.349440        0.0   

                       rewards  
time                            
2022-01-01 00:00:00  15.000000  
2022-01-01 00:15:00  15.000000  
2022-01-01 00:30:00  15.000000  
2022-01-01 00:45:00  15.000000  
2022-01-01 01:00:00  15.000000  
...                        ...  
2022-06-06 04:45:00  -5.283105  
2022-06-06 05:00:00  15.000000  
2022-06-06 05:15:00  -4.955673  
2022-06-06 05:30:00  -4.892805  
20

In [25]:
#env.plot_Elvis_results()

In [26]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [27]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [28]:
env.plot_VPP_Elvis_comparison()

In [29]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [30]:
env.plot_rewards_stats()

In [31]:
env.plot_EVs_kpi()

In [32]:
env.plot_load_kpi()

In [33]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Validating dataset VPP Simulation using the loaded trained model

In [34]:
#VALIDATING Environment initialization
env = VPPEnv(VPP_validating_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 5217, Arrival time: 2022-01-01 03:00:00, Parking_time: 24, Leaving_time: 2022-01-02 03:00:00, SOC: 0.4879902182817486, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 6520, Arrival time: 2022-12-31 20:45:00, Parking_time: 23.093063873974202, Leaving_time: 2023-01-01 19:50:35.029946, SOC: 0.4574776142522687, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -30085.39 , over-consume=kWh  2136.67 , under-consume=kWh  -32222.06 , Total_cost=€  -1187.15 , overcost=€  113.34
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  16954.36 , over-consume=kWh  37835.65 , under-consume=kWh  20881.29 , Total_cost=€  787.8 , overcost=€  1648.82 , Charging_events=  1304 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  74.71


In [35]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

Output hidden; open in https://colab.research.google.com to view.

In [36]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [37]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  19244.08 , over-consume=kWh  39862.84 , under-consume=kWh  20618.76 , Total_cost=€  896.43 , overcost=€  1749.4 , Av.EV_en_left=kWh  100.0 , Charging_events=  1304 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  74.71
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -4482.99 , over-consume=KWh  812.78 , under-consume=KWh  5295.77 , Total_cost=€  -178.92 , Overcost=€  34.54 
 EV_INFO: Av.EV_energy_leaving=kWh  69.6 , Std.EV_energy_leaving=kWh  23.61 , EV_departures =  1299 , EV_queue_left =  1
SCORE:  Cumulative_reward= 470462.9 - Step_rewars (load_t= 403038.51, EVs_energy_t= 30524.69)
 - Final_rewards (EVs_energy= 21732.75, Overconsume= -15.9, Underconsume= -1065.8, Overcost= 16248.63)
Episode:1 Score:470462.89808646473


In [38]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [39]:
VPP_table.head(15000)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:15:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:30:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:45:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 01:00:00   0.000000   0.000000   0.000000   0.000000   
...                        ...        ...        ...        ...   
2022-06-06 04:45:00  82.191597  62.690834  65.294830  79.150909   
2022-06-06 05:00:00  83.506149  62.440834  66.609383  80.465462   
2022-06-06 05:15:00  84.831062  62.190834  67.934296  81.790375   
2022-06-06 05:30:00  86.070305  61.940834  69.173538  83.029617   
2022-06-06 05:45:00  87.363068  61.690834  70.466301  84.322380   

                                       EVs_id       actions  \
time                                                          
2022-01-01 00:00:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:15:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:30:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:45:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 01:00:00              [0, 0, 0, 0]  [2, 0, 1, 0]   
...                                       ...           ...   
2022-06-06 04:45:00  [8367, 8365, 8366, 8368]  [1, 2, 1, 1]   
2022-06-06 05:00:00  [8367, 8365, 8366, 8368]  [1, 2, 1, 1]   
2022-06-06 05:15:00  [8367, 8365, 8366, 8368]  [1, 2, 1, 1]   
2022-06-06 05:30:00  [8367, 8365, 8366, 8368]  [1, 2, 1, 1]   
2022-06-06 05:45:00  [8367, 8365, 8366, 8368]  [1, 2, 1, 1]   

                                      mask_truth  ev_charged_pwr  \
time                                                               
2022-01-01 00:00:00  [False, False, False, True]        0.000000   
2022-01-01 00:15:00  [False, False, False, True]        0.000000   
2022-01-01 00:30:00  [False, False, False, True]        0.000000   
2022-01-01 00:45:00  [False, False, False, True]        0.000000   
2022-01-01 01:00:00   [False, True, False, True]        0.000000   
...                                          ...             ...   
2022-06-06 04:45:00    [True, False, True, True]       11.529988   
2022-06-06 05:00:00    [True, False, True, True]       15.774583   
2022-06-06 05:15:00    [True, False, True, True]       15.898930   
2022-06-06 05:30:00    [True, False, True, True]       14.870906   
2022-06-06 05:45:00    [True, False, True, True]       15.513184   

                     ev_discharged_pwr      load  load_reward  EV_reward  \
time                                                                       
2022-01-01 00:00:00                0.0 -3.525525    -3.672272        0.0   
2022-01-01 00:15:00                0.0 -3.203363    -4.441672        0.0   
2022-01-01 00:30:00                0.0 -3.665003    -3.405043        0.0   
2022-01-01 00:45:00                0.0 -3.043026    -5.310902        0.0   
2022-01-01 01:00:00                0.0 -4.341992    -5.296099        0.0   
...                                ...       ...          ...        ...   
2022-06-06 04:45:00               -1.0  0.000000    15.000000        0.0   
2022-06-06 05:00:00               -1.0  0.000000    15.000000        0.0   
2022-06-06 05:15:00               -1.0  0.000000    15.000000        0.0   
2022-06-06 05:30:00               -1.0  0.000000    15.000000        0.0   
2022-06-06 05:45:00               -1.0  0.000000    15.000000        0.0   

                       rewards  
time                            
2022-01-01 00:00:00  -3.672272  
2022-01-01 00:15:00  -4.441672  
2022-01-01 00:30:00  -3.405043  
2022-01-01 00:45:00  -5.310902  
2022-01-01 01:00:00  -5.296099  
...                        ...  
2022-06-06 04:45:00  15.000000  
2022-06-06 05:00:00  15.000000  
2022-06-06 05:15:00  15.000000  
2022-06-06 05:30:00  15.000000  
2022-06-06 05:45:00  15.000000  

[15000 rows x 13 columns]

In [40]:
env.plot_VPP_results()


Output hidden; open in https://colab.research.google.com to view.

In [41]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [42]:
env.plot_VPP_Elvis_comparison()

In [43]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [44]:
env.plot_rewards_stats()

In [45]:
env.plot_EVs_kpi()

In [46]:
env.plot_load_kpi()

In [47]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Training dataset VPP Simulation using the loaded trained model

In [48]:
#TRAINING Environment initialization
env = VPPEnv(VPP_training_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 9129, Arrival time: 2022-01-01 08:15:00, Parking_time: 23.491675521380916, Leaving_time: 2022-01-02 07:44:30.031877, SOC: 0.5599819356522051, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 10432, Arrival time: 2022-12-31 14:45:00, Parking_time: 24, Leaving_time: 2023-01-01 14:45:00, SOC: 0.4733853732428758, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -34117.7 , over-consume=kWh  1556.25 , under-consume=kWh  -35673.95 , Total_cost=€  -1196.64 , overcost=€  97.86
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  14260.12 , over-consume=kWh  36117.61 , under-consume=kWh  21857.49 , Total_cost=€  713.03 , overcost=€  1522.67 , Charging_events=  1304 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  77.36


In [49]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

Output hidden; open in https://colab.research.google.com to view.

In [50]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [51]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  13343.33 , over-consume=kWh  36001.15 , under-consume=kWh  22657.83 , Total_cost=€  672.69 , overcost=€  1501.08 , Av.EV_en_left=kWh  100.0 , Charging_events=  1304 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  77.36
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -6680.7 , over-consume=KWh  805.6 , under-consume=KWh  7486.29 , Total_cost=€  -222.9 , Overcost=€  34.68 
 EV_INFO: Av.EV_energy_leaving=kWh  71.84 , Std.EV_energy_leaving=kWh  23.3 , EV_departures =  1301 , EV_queue_left =  0
SCORE:  Cumulative_reward= 448455.6 - Step_rewars (load_t= 374383.12, EVs_energy_t= 39068.8)
 - Final_rewards (EVs_energy= 21935.43, Overconsume= -97.02, Underconsume= -2445.12, Overcost= 15610.39)
Episode:1 Score:448455.60452213325


In [52]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [53]:
VPP_table.head(14995)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:15:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:30:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:45:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 01:00:00   0.000000   0.000000   0.000000   0.000000   
...                        ...        ...        ...        ...   
2022-06-06 03:30:00  54.874504  44.654285  23.731766  72.276527   
2022-06-06 03:45:00  55.508152  44.404285  23.481766  72.910172   
2022-06-06 04:00:00  56.557949  44.154285  23.231766  73.959969   
2022-06-06 04:15:00  57.529007  43.904285  22.981766  74.931023   
2022-06-06 04:30:00  58.563766   0.000000  22.731766  75.965782   

                                           EVs_id       actions  \
time                                                              
2022-01-01 00:00:00                  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:15:00                  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:30:00                  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:45:00                  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 01:00:00                  [0, 0, 0, 0]  [2, 0, 1, 0]   
...                                           ...           ...   
2022-06-06 03:30:00  [12286, 12285, 12287, 12288]  [1, 2, 2, 1]   
2022-06-06 03:45:00  [12286, 12285, 12287, 12288]  [1, 2, 2, 1]   
2022-06-06 04:00:00  [12286, 12285, 12287, 12288]  [1, 2, 2, 1]   
2022-06-06 04:15:00  [12286, 12285, 12287, 12288]  [1, 2, 2, 1]   
2022-06-06 04:30:00      [12286, 0, 12287, 12288]  [1, 2, 1, 2]   

                                      mask_truth  ev_charged_pwr  \
time                                                               
2022-01-01 00:00:00  [False, False, False, True]        0.000000   
2022-01-01 00:15:00  [False, False, False, True]        0.000000   
2022-01-01 00:30:00  [False, False, False, True]        0.000000   
2022-01-01 00:45:00  [False, False, False, True]        0.000000   
2022-01-01 01:00:00   [False, True, False, True]        0.000000   
...                                          ...             ...   
2022-06-06 03:30:00   [True, False, False, True]        5.959670   
2022-06-06 03:45:00   [True, False, False, True]        5.069172   
2022-06-06 04:00:00   [True, False, False, True]        8.398383   
2022-06-06 04:15:00   [True, False, False, True]        7.768449   
2022-06-06 04:30:00   [True, False, True, False]        8.278071   

                     ev_discharged_pwr          load  load_reward  EV_reward  \
time                                                                           
2022-01-01 00:00:00                0.0 -3.551087e+00    -4.878791   0.000000   
2022-01-01 00:15:00                0.0 -3.927275e+00    -4.744162   0.000000   
2022-01-01 00:30:00                0.0 -3.846497e+00    -4.558597   0.000000   
2022-01-01 00:45:00                0.0 -3.735158e+00    -6.485303   0.000000   
2022-01-01 01:00:00                0.0 -5.633833e+00    -5.318256   0.000000   
...                                ...           ...          ...        ...   
2022-06-06 03:30:00               -2.0 -4.440892e-16    15.000000   0.000000   
2022-06-06 03:45:00               -2.0  0.000000e+00    15.000000   0.000000   
2022-06-06 04:00:00               -2.0  0.000000e+00    15.000000   0.000000   
2022-06-06 04:15:00               -2.0  0.000000e+00    15.000000 -72.997716   
2022-06-06 04:30:00               -2.0  0.000000e+00    15.000000   0.000000   

                       rewards  
time                            
2022-01-01 00:00:00  -4.878791  
2022-01-01 00:15:00  -4.744162  
2022-01-01 00:30:00  -4.558597  
2022-01-01 00:45:00  -6.485303  
2022-01-01 01:00:00  -5.318256  
...                        ...  
2022-06-06 03:30:00  15.000000  
2022-06-06 03:45:00  15.000000  
2022-06-06 04:00:00  15.00000

In [54]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [55]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [56]:
env.plot_VPP_Elvis_comparison()

In [57]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [58]:
env.plot_rewards_stats()

In [59]:
env.plot_EVs_kpi()

In [60]:
env.plot_actions_kpi()

In [61]:
env.plot_load_kpi()

In [62]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [63]:
#env.close()